In [1]:
import tensorflow as tf
import pandas as pd
from numpy import array
import nengo
import numpy as np
import nengo_dl
import matplotlib.pyplot as plt

In [2]:

from urllib.request import urlretrieve

import matplotlib.pyplot as plt
import nengo
from nengo.utils.filter_design import cont2discrete
import numpy as np
import tensorflow as tf

import nengo_dl

#### Dummy regression Dataset 3 inputs 1 output
#### build a model to predict y_test values given x_test values

In [156]:
x_train = array([[[0.16240086],
        [0.13572511],
        [0.12298894]],

       [[0.13573571],
        [0.12298894],
        [0.1394957 ]],

       [[0.12299854],
        [0.1394957 ],
        [0.16518061]],

       [[0.13950658],
        [0.16518061],
        [0.15289813]],

       [[0.1651935 ],
        [0.15289813],
        [0.14116833]],

       [[0.15291007],
        [0.14116833],
        [0.1374616 ]],

       [[0.14117935],
        [0.1374616 ],
        [0.12912672]],

       [[0.13747232],
        [0.12912672],
        [0.11594404]],

       [[0.1291368 ],
        [0.11594404],
        [0.13490303]],

       [[0.11595309],
        [0.13490303],
        [0.13712141]],
                 
       [[0.13491356],
        [0.13712141],
        [0.14390409]],

       [[0.13713211],
        [0.14390409],
        [0.16589645]],

       [[0.14391532],
        [0.16589645],
        [0.15786646]],

       [[0.1659094 ],
        [0.15786646],
        [0.16160157]],

       [[0.15787878],
        [0.16160157],
        [0.14208264]],

       [[0.16161418],
        [0.14208264],
        [0.12267004]],

       [[0.14209373],
        [0.12267004],
        [0.13620001]],

       [[0.12267962],
        [0.13620001],
        [0.11758829]],

       [[0.13621063],
        [0.11758829],
        [0.13591649]],

       [[0.11759747],
        [0.13591649],
        [0.15659777]]])

y_train = array([[[0.1394957 ]],

               [[0.16518061]],

               [[0.15289813]],

               [[0.14116833]],

               [[0.1374616 ]],

               [[0.12912672]],

               [[0.11594404]],

               [[0.13490303]],

               [[0.13712141]],

               [[0.14390409]],
                 
               [[0.1394957 ]],

               [[0.16518061]],

               [[0.15289813]],

               [[0.14116833]],

               [[0.1374616 ]],

               [[0.12912672]],

               [[0.11594404]],

               [[0.13490303]],

               [[0.13712141]],

               [[0.14390409]]])


x_test = array([[[0.41645002],
                [0.36998038],
                [0.45262021]],

               [[0.37000926],
                [0.45262021],
                [0.46759614]],

               [[0.45265554],
                [0.46759614],
                [0.46540604]]])


y_test = array([[[0.46759614]],
                [[0.46540604]],
                [[0.48036778]]])

In [157]:
print(x_train.shape)
print(y_train.shape)
print(x_test.shape)
print(y_test.shape)

(20, 3, 1)
(20, 1, 1)
(3, 3, 1)
(3, 1, 1)


# Normal LMU with Tanh activation

Produces good results

In [127]:
class LMUCell(nengo.Network):
    def __init__(self, units, order, theta, input_d, **kwargs):
        super().__init__(**kwargs)

        # compute the A and B matrices according to the LMU's mathematical derivation
        # (see the paper for details)
        Q = np.arange(order, dtype=np.float64)
        R = (2 * Q + 1)[:, None] / theta
        j, i = np.meshgrid(Q, Q)

        A = np.where(i < j, -1, (-1.0) ** (i - j + 1)) * R
        B = (-1.0) ** Q[:, None] * R
        C = np.ones((1, order))
        D = np.zeros((1,))
        
#          here we are using zero-order hold(zoh) method to 
#        discretize the value of A and B 
        A, B, _, _, _ = cont2discrete((A, B, C, D), dt=1.0, method="zoh")

        with self:
            nengo_dl.configure_settings(trainable=None)

            # create objects corresponding to the x/u/m/h variables in the above diagram
            self.x = nengo.Node(size_in=input_d)
            self.u = nengo.Node(size_in=1)
            self.m = nengo.Node(size_in=order)
            self.h = nengo_dl.TensorNode(tf.nn.tanh, shape_in=(units,), pass_time=False)
    #             self.h = nengo.Ensemble(units, 1, 
    #                                     neuron_type=nengo.RegularSpiking(nengo.Tanh(tau_ref=0.01)), 
    #                                     gain=np.ones(units), bias=np.zeros(units)).neurons  
            # compute u_t from the above diagram. we have removed e_h and e_m as they
            # are not needed in this task.
            nengo.Connection(
                self.x, self.u, transform=np.ones((1, input_d)), synapse=None
            )

            # compute m_t
            # in this implementation we'll make A and B non-trainable, but they
            # could also be optimized in the same way as the other parameters.
            # note that setting synapse=0 (versus synapse=None) adds a one-timestep
            # delay, so we can think of any connections with synapse=0 as representing
            # value_{t-1}.
            conn_A = nengo.Connection(self.m, self.m, transform=A, synapse=0)
            self.config[conn_A].trainable = False
            conn_B = nengo.Connection(self.u, self.m, transform=B, synapse=None)
            self.config[conn_B].trainable = False

            # compute h_t
            nengo.Connection(
                self.x, self.h, transform=nengo_dl.dists.Glorot(), synapse=None
            )
            nengo.Connection(
                self.h, self.h, transform=nengo_dl.dists.Glorot(), synapse=0
            )
            nengo.Connection(
                self.m,
                self.h,
                transform=nengo_dl.dists.Glorot(),
                synapse=None,
            )
            
            
# Training the Normal LMU

with nengo.Network(seed=0) as net:
    nengo_dl.configure_settings(
        trainable=None,
        stateful=None,
        keep_history=False,
    )

    inp = nengo.Node((np.zeros(x_train.shape[-1])))

    lmu = LMUCell(
        units=32,
        order=16,
        theta=x_train.shape[1],
        input_d=x_train.shape[-1],
    )
    
    conn = nengo.Connection(inp, lmu.x, synapse=None)
    net.config[conn].trainable = False 

    out = nengo.Node(size_in=1) #changed to 1
    nengo.Connection(lmu.h, out,transform=nengo_dl.dists.Glorot(), synapse=None)
   
    p = nengo.Probe(out, label = "output")   

    
with nengo_dl.Simulator(net) as sim:
    sim.compile(
        loss=tf.losses.mse,
        optimizer=tf.optimizers.Adam(learning_rate=0.001),
    )
    sim.keras_model.summary()
    trainning_history = sim.fit(x_train, y_train, epochs=10)
    

    output_x = sim.predict(x_test)
    # the output is in a dict form, so get the values from the output probe
    # which is the first value of the dictionary
    x_test_predictions = list(output_x.values())[0]

    print()

Build finished in 0:00:00                                                      
Optimization finished in 0:00:00                                               
Construction finished in 0:00:00                                               
Model: "keras_model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
node (InputLayer)               [(1, None, 3)]       0                                            
__________________________________________________________________________________________________
n_steps (InputLayer)            [(1, 1)]             0                                            
__________________________________________________________________________________________________
TensorGraph (TensorGraph)       [(1, None, 1), (1,)] 1939        node[0][0]                       
                                              

/home/wolf/Dropbox/code/nengo-dl/nengo_dl/simulator.py:1024: UserWarning: Running for one timestep, but the network contains synaptic filters (which will introduce at least a one-timestep delay); did you mean to set synapse=None?
  warnings.warn(


20/20 [==============================] - 2s 1ms/step - loss: 0.0769 - output_loss: 0.0769
Epoch 2/10
20/20 [==============================] - 0s 1ms/step - loss: 0.0115 - output_loss: 0.0115
Epoch 3/10
20/20 [==============================] - 0s 1ms/step - loss: 4.5547e-04 - output_loss: 4.5547e-04
Epoch 4/10
20/20 [==============================] - 0s 2ms/step - loss: 3.3367e-04 - output_loss: 3.3367e-04
Epoch 5/10
20/20 [==============================] - 0s 1ms/step - loss: 2.8153e-04 - output_loss: 2.8153e-04
Epoch 6/10
20/20 [==============================] - 0s 1ms/step - loss: 1.3569e-04 - output_loss: 1.3569e-04
Epoch 7/10
20/20 [==============================] - 0s 1ms/step - loss: 2.4364e-04 - output_loss: 2.4364e-04
Epoch 8/10
20/20 [==============================] - 0s 2ms/step - loss: 3.0855e-04 - output_loss: 3.0855e-04
Epoch 9/10
20/20 [==============================] - 0s 1ms/step - loss: 1.6421e-04 - output_loss: 1.6421e-04
Epoch 10/10
20/20 [===========================

##### Result of Normal LMU

results are good

In [128]:
print(f'Predicted values are: {x_test_predictions.T}')
print(f'True values are: {y_test.T}')
from sklearn.metrics import mean_squared_error
error = np.sqrt(mean_squared_error(y_test.reshape(3,1), x_test_predictions.reshape(3,1)))
print(f'The RMSE error of Normal LMU is {error}')

Predicted values are: [[[0.3785053  0.42028445 0.41257465]]]
True values are: [[[0.46759614 0.46540604 0.48036778]]]
The RMSE error of Normal LMU is 0.06968750759038828


# Spiking LMU with tanh 

In [129]:
# Lmu Cell 

In [130]:
class LMUCell(nengo.Network):
    def __init__(self, units, order, theta, input_d, **kwargs):
        super().__init__(**kwargs)

        # compute the A and B matrices according to the LMU's mathematical derivation
        # (see the paper for details)
        Q = np.arange(order, dtype=np.float64)
        R = (2 * Q + 1)[:, None] / theta
        j, i = np.meshgrid(Q, Q)

        A = np.where(i < j, -1, (-1.0) ** (i - j + 1)) * R
        B = (-1.0) ** Q[:, None] * R
        C = np.ones((1, order))
        D = np.zeros((1,))
        
#          here we are using zero-order hold(zoh) method to 
#        discretize the value of A and B 
        A, B, _, _, _ = cont2discrete((A, B, C, D), dt=1.0, method="zoh")

        with self:
            nengo_dl.configure_settings(trainable=None)

            # create objects corresponding to the x/u/m/h variables in the above diagram
            self.x = nengo.Node(size_in=input_d)
            self.u = nengo.Node(size_in=1)
            self.m = nengo.Node(size_in=order)
#             self.h = nengo_dl.TensorNode(tf.nn.relu, shape_in=(units,), pass_time=False)
            self.h = nengo.Ensemble(units, 1, 
                                    #neuron_type=nengo.RegularSpiking(nengo.Tanh(tau_ref=0.001)), 
                                    neuron_type=nengo.Tanh(tau_ref=1), 
                                    gain=np.ones(units), bias=np.zeros(units)).neurons  

#             compute u_t from the above diagram. we have removed e_h and e_m as they
#             are not needed in this task.
            nengo.Connection(
                self.x,
                self.u,
                transform=np.ones((1, input_d)),
                synapse=None,
            )

            # compute m_t
            # in this implementation we'll make A and B non-trainable, but they
            # could also be optimized in the same way as the other parameters.
            # note that setting synapse=0 (versus synapse=None) adds a one-timestep
            # delay, so we can think of any connections with synapse=0 as representing
            # value_{t-1}.
            conn_A = nengo.Connection(
                self.m,
                self.m,
                transform=A,
                synapse=0,
            )
            self.config[conn_A].trainable = False
            
            conn_B = nengo.Connection(
                self.u,
                self.m,
                transform=B,
                synapse=None,
            )
            self.config[conn_B].trainable = False

            # compute h_t
            nengo.Connection(
                self.x,
                self.h,
                transform=nengo_dl.dists.Glorot(),
                synapse=None,
            )
            nengo.Connection(
                self.h,
                self.h,
                transform=nengo_dl.dists.Glorot(),
                synapse=0,
            )
            nengo.Connection(
                self.m,
                self.h,
                transform=nengo_dl.dists.Glorot(),
                synapse=None,
            )
            
            

# Experiment 1 - training like normal LMU

predicts [0] as output for all test samples

In [131]:
with nengo.Network(seed=0) as net:
    nengo_dl.configure_settings(
        trainable=None,
        stateful=None,
        keep_history=False,
    )

    inp = nengo.Node((np.zeros(x_train.shape[-1])))

    lmu = LMUCell(
        units=32,
        order=16,
        theta=x_train.shape[1],
        input_d=x_train.shape[-1],
    )
    net.config[lmu.h.ensemble].trainable = False
    
    conn = nengo.Connection(inp, lmu.x, synapse=None)
    net.config[conn].trainable = False 

    out = nengo.Node(size_in=1) #changed to 1
    nengo.Connection(lmu.h, out, transform=nengo_dl.dists.Glorot(), synapse=None)
   
    p = nengo.Probe(out, label = "output")   
    
with nengo_dl.Simulator(net) as sim:
    sim.compile(
        loss=tf.losses.mse,
        optimizer=tf.optimizers.Adam(learning_rate=0.001),
    )
    sim.keras_model.summary()
    trainning_history = sim.fit(x_train, y_train, epochs=10)
    
    output_x = sim.predict(x_test)
    # the output is in a dict form, so get the values from the output probe
    # which is the first value of the dictionary
    x_test_predictions = list(output_x.values())[0]

Build finished in 0:00:00                                                      
Optimization finished in 0:00:00                                               
|##############Constructing graph: build stage (29%)             | ETA: 0:00:00

/home/wolf/Dropbox/code/nengo-dl/nengo_dl/simulator.py:460: UserWarning: No GPU support detected. See https://www.nengo.ai/nengo-dl/installation.html#installing-tensorflow for instructions on setting up TensorFlow with GPU support.
  warnings.warn(


Construction finished in 0:00:00                                               
Model: "keras_model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
node (InputLayer)               [(1, None, 3)]       0                                            
__________________________________________________________________________________________________
n_steps (InputLayer)            [(1, 1)]             0                                            
__________________________________________________________________________________________________
TensorGraph (TensorGraph)       [(1, None, 1), (1,)] 1939        node[0][0]                       
                                                                 n_steps[0][0]                    
Total params: 1,939
Trainable params: 1,667
Non-trainable params: 272
_____________________________________

/home/wolf/Dropbox/code/nengo-dl/nengo_dl/simulator.py:1024: UserWarning: Running for one timestep, but the network contains synaptic filters (which will introduce at least a one-timestep delay); did you mean to set synapse=None?
  warnings.warn(


20/20 [==============================] - 2s 1ms/step - loss: 0.0769 - output_loss: 0.0769
Epoch 2/10
20/20 [==============================] - 0s 1ms/step - loss: 0.0115 - output_loss: 0.0115
Epoch 3/10
20/20 [==============================] - 0s 2ms/step - loss: 4.5547e-04 - output_loss: 4.5547e-04
Epoch 4/10
20/20 [==============================] - 0s 2ms/step - loss: 3.3367e-04 - output_loss: 3.3367e-04
Epoch 5/10
20/20 [==============================] - 0s 2ms/step - loss: 2.8153e-04 - output_loss: 2.8153e-04
Epoch 6/10
20/20 [==============================] - 0s 1ms/step - loss: 1.3569e-04 - output_loss: 1.3569e-04
Epoch 7/10
20/20 [==============================] - 0s 2ms/step - loss: 2.4364e-04 - output_loss: 2.4364e-04
Epoch 8/10
20/20 [==============================] - 0s 2ms/step - loss: 3.0855e-04 - output_loss: 3.0855e-04
Epoch 9/10
20/20 [==============================] - 0s 1ms/step - loss: 1.6421e-04 - output_loss: 1.6421e-04
Epoch 10/10
20/20 [===========================

#### Results for Experiment 1

In [132]:
print(f'Predicted values are: {x_test_predictions.T}')
print(f'True values are: {y_test.T}')
from sklearn.metrics import mean_squared_error
error = np.sqrt(mean_squared_error(y_test.reshape(3,1),x_test_predictions.reshape(3,1)))
print(f'The RMSE error of Experiment 1 is {error}')

Predicted values are: [[[0.3785053  0.42028445 0.41257465]]]
True values are: [[[0.46759614 0.46540604 0.48036778]]]
The RMSE error of Experiment 1 is 0.06968750759038828
